## Install dependencies

In [1]:
%pip install -r requirements.txt

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import pandas as pd
from pymongo import MongoClient
from pyspark.sql import SparkSession
import os
from pyspark.sql.functions import year
import time

## Insert data into Mongodb

The datasets are currently files in .csv format, we have to import them into Mondodb

In [3]:
'''Insert ratings.csv into MongoDB'''
# load csv file into pandas DataFrame first
df = pd.read_csv("dataset/ml-latest-small/ratings.csv")

# =specify Mongodb client, database and collection
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

# convert DataFrame to a list of dictionaries (one for each row)
data = df.to_dict(orient="records")

# insert data into MongoDB
collection.insert_many(data)

InsertManyResult([ObjectId('6741ac0a6a48f55e41b8851e'), ObjectId('6741ac0a6a48f55e41b8851f'), ObjectId('6741ac0a6a48f55e41b88520'), ObjectId('6741ac0a6a48f55e41b88521'), ObjectId('6741ac0a6a48f55e41b88522'), ObjectId('6741ac0a6a48f55e41b88523'), ObjectId('6741ac0a6a48f55e41b88524'), ObjectId('6741ac0a6a48f55e41b88525'), ObjectId('6741ac0a6a48f55e41b88526'), ObjectId('6741ac0a6a48f55e41b88527'), ObjectId('6741ac0a6a48f55e41b88528'), ObjectId('6741ac0a6a48f55e41b88529'), ObjectId('6741ac0a6a48f55e41b8852a'), ObjectId('6741ac0a6a48f55e41b8852b'), ObjectId('6741ac0a6a48f55e41b8852c'), ObjectId('6741ac0a6a48f55e41b8852d'), ObjectId('6741ac0a6a48f55e41b8852e'), ObjectId('6741ac0a6a48f55e41b8852f'), ObjectId('6741ac0a6a48f55e41b88530'), ObjectId('6741ac0a6a48f55e41b88531'), ObjectId('6741ac0a6a48f55e41b88532'), ObjectId('6741ac0a6a48f55e41b88533'), ObjectId('6741ac0a6a48f55e41b88534'), ObjectId('6741ac0a6a48f55e41b88535'), ObjectId('6741ac0a6a48f55e41b88536'), ObjectId('6741ac0a6a48f55e41b885

In [4]:
'''Insert movies.csv into MongoDB'''
file_path = os.path.join('dataset', 'ml-latest-small', 'movies.csv')

df = pd.read_csv(file_path)

client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["movies"]

data = df.to_dict(orient="records")
collection.insert_many(data)

InsertManyResult([ObjectId('6741ac0b6a48f55e41ba0f03'), ObjectId('6741ac0b6a48f55e41ba0f04'), ObjectId('6741ac0b6a48f55e41ba0f05'), ObjectId('6741ac0b6a48f55e41ba0f06'), ObjectId('6741ac0b6a48f55e41ba0f07'), ObjectId('6741ac0b6a48f55e41ba0f08'), ObjectId('6741ac0b6a48f55e41ba0f09'), ObjectId('6741ac0b6a48f55e41ba0f0a'), ObjectId('6741ac0b6a48f55e41ba0f0b'), ObjectId('6741ac0b6a48f55e41ba0f0c'), ObjectId('6741ac0b6a48f55e41ba0f0d'), ObjectId('6741ac0b6a48f55e41ba0f0e'), ObjectId('6741ac0b6a48f55e41ba0f0f'), ObjectId('6741ac0b6a48f55e41ba0f10'), ObjectId('6741ac0b6a48f55e41ba0f11'), ObjectId('6741ac0b6a48f55e41ba0f12'), ObjectId('6741ac0b6a48f55e41ba0f13'), ObjectId('6741ac0b6a48f55e41ba0f14'), ObjectId('6741ac0b6a48f55e41ba0f15'), ObjectId('6741ac0b6a48f55e41ba0f16'), ObjectId('6741ac0b6a48f55e41ba0f17'), ObjectId('6741ac0b6a48f55e41ba0f18'), ObjectId('6741ac0b6a48f55e41ba0f19'), ObjectId('6741ac0b6a48f55e41ba0f1a'), ObjectId('6741ac0b6a48f55e41ba0f1b'), ObjectId('6741ac0b6a48f55e41ba0f

## Use Apache Spark for parallel data processing

### Initial a Spark Session

In [5]:
# spark = SparkSession.builder \
#     .appName("Big-Data-Demo") \
#     .master("local[*]") \
#     .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
#     .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/")  \
#     .getOrCreate() \
    
spark = SparkSession.builder \
    .appName("Big-Data-Demo") \
    .master("local[*]") \
    .config("spark.jars.packages", "org.mongodb.spark:mongo-spark-connector_2.12:3.0.1") \
    .config("spark.mongodb.read.connection.uri", "mongodb://127.0.0.1:27017/") \
    .getOrCreate() \

print(f"----------spark version: {spark.version}------------")

----------spark version: 3.5.3------------


### Load data from MongoDB

#### Load all data from a collection

In [ ]:
# load all data from MongoDB
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .load()    

df_movies = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.movies")\
    .option("database", "test")\
    .option("collection", "movies")\
    .load()   

# Show the loaded data
print(f"Original Rating Data:")
print(df_ratings.show())
print(f"Original Movie Data:")
print( df_movies.show())

Original Rating Data:
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6731d74e5d382ee9...|      1|   4.0|964982703|     1|
|{6731d74e5d382ee9...|      3|   4.0|964981247|     1|
|{6731d74e5d382ee9...|      6|   4.0|964982224|     1|
|{6731d74e5d382ee9...|     47|   5.0|964983815|     1|
|{6731d74e5d382ee9...|     50|   5.0|964982931|     1|
|{6731d74e5d382ee9...|     70|   3.0|964982400|     1|
|{6731d74e5d382ee9...|    101|   5.0|964980868|     1|
|{6731d74e5d382ee9...|    110|   4.0|964982176|     1|
|{6731d74e5d382ee9...|    151|   5.0|964984041|     1|
|{6731d74e5d382ee9...|    157|   5.0|964984100|     1|
|{6731d74e5d382ee9...|    163|   5.0|964983650|     1|
|{6731d74e5d382ee9...|    216|   5.0|964981208|     1|
|{6731d74e5d382ee9...|    223|   3.0|964980985|     1|
|{6731d74e5d382ee9...|    231|   5.0|964981179|     1|
|{6731d74e5d382ee9...|    235|   4.0|964980

#### Make query to the database

In [7]:
# sol 1: failed, maybe because of the version of the spark
query = '{"rating": {"$gt": 4}}'
print(f"Query sent to MongoDB: {query}")

# Load filtered data
df_ratings_filtered = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/")\
    .option("database", "test")\
    .option("collection", "ratings")\
    .option("query", query)\
    .load()

# Show filtered data
print("Filtered Data (movies with rating > 4):")
df_ratings_filtered.show()
query = '{"rating": {"$gt": 4}}'

Query sent to MongoDB: {"rating": {"$gt": 4}}
Filtered Data (movies with rating > 4):
+--------------------+-------+------+---------+------+
|                 _id|movieId|rating|timestamp|userId|
+--------------------+-------+------+---------+------+
|{6731d74e5d382ee9...|      1|   4.0|964982703|     1|
|{6731d74e5d382ee9...|      3|   4.0|964981247|     1|
|{6731d74e5d382ee9...|      6|   4.0|964982224|     1|
|{6731d74e5d382ee9...|     47|   5.0|964983815|     1|
|{6731d74e5d382ee9...|     50|   5.0|964982931|     1|
|{6731d74e5d382ee9...|     70|   3.0|964982400|     1|
|{6731d74e5d382ee9...|    101|   5.0|964980868|     1|
|{6731d74e5d382ee9...|    110|   4.0|964982176|     1|
|{6731d74e5d382ee9...|    151|   5.0|964984041|     1|
|{6731d74e5d382ee9...|    157|   5.0|964984100|     1|
|{6731d74e5d382ee9...|    163|   5.0|964983650|     1|
|{6731d74e5d382ee9...|    216|   5.0|964981208|     1|
|{6731d74e5d382ee9...|    223|   3.0|964980985|     1|
|{6731d74e5d382ee9...|    231|   5

In [21]:
# set format as "mongo" instead of "mongodb", set uri
start_time = time.time()
df_ratings_filtered = spark.read.format("mongo").option("uri", "mongodb://127.0.0.1:27017/") \
                 .option("database", "test") \
                 .option("collection", "ratings") \
                 .load()

df_ratings_filtered.filter(df_ratings_filtered['rating'] > 4)
end_time = time.time()
df_ratings_filtered.head()
print(f"Execution time: {end_time - start_time} seconds")

Execution time: 0.23384332656860352 seconds


In [28]:
# sol 2: return cursors points to rows in the collection
start_time = time.time()
client = MongoClient('mongodb://localhost:27017/')
db = client["test"]
collection = db["ratings"]

query = {"rating": {"$gt": 4}}  # Find documents where age > 25
cursors = collection.find(query)

# for doc in results:
#     print(doc)

stop_time1 = time.time()

# filtered_df = pd.DataFrame(list(cursors))
# stop_time = time.time()
# filtered_df.head()
# print(f"Time taken to fetch data from MongoDB: {stop_time1 - start_time}")
# print(f"Total time taken: {stop_time - start_time}")
# cursors = list(cursors)
# print(cursors[0]['userId', 'movieId', 'rating', 'timestamp'])

filtered_df = spark.createDataFrame(list(cursors))
filtered_df.show()

PySparkTypeError: [CANNOT_INFER_TYPE_FOR_FIELD] Unable to infer the type of the field `_id`.

In [11]:
# sol 3: get the dataframe, then filter it using pandas => worse than using MongoDB query
start_time = time.time()
df_ratings = spark.read.format("mongo")\
    .option("uri", "mongodb://127.0.0.1:27017/test.ratings")\
    .load()

df_ratings_pd = df_ratings.toPandas()
df_ratings_pd = df_ratings_pd[df_ratings_pd['rating'] > 4]

df_ratings_pd.head()
stop_time = time.time()
print(f"Time taken: {stop_time - start_time}")

Time taken: 73.94256544113159


### Spark's dataframe operations

In [12]:
# df_movies.show()
# df_ratings.show()

joined_df = df_movies.join(df_ratings, on="movieId", how="right")
print(f"movies_ratings_df:")
# print(joined_df.columns)
# print(joined_df.select("timestamp").show())
# print(type(joined_df))
joined_df.show()

movies_ratings_df:
+-------+--------------------+----------------+--------------------+--------------------+------+----------+------+
|movieId|                 _id|          genres|               title|                 _id|rating| timestamp|userId|
+-------+--------------------+----------------+--------------------+--------------------+------+----------+------+
|     47|{6731d7505d382ee9...|Mystery|Thriller|Seven (a.k.a. Se7...|{6731d74e5d382ee9...|   5.0| 964983815|     1|
|     47|{6731dfbf0e8d3b5f...|Mystery|Thriller|Seven (a.k.a. Se7...|{6731d74e5d382ee9...|   5.0| 964983815|     1|
|     47|{6731e675babbfbf7...|Mystery|Thriller|Seven (a.k.a. Se7...|{6731d74e5d382ee9...|   5.0| 964983815|     1|
|     47|{6731e730356e73e5...|Mystery|Thriller|Seven (a.k.a. Se7...|{6731d74e5d382ee9...|   5.0| 964983815|     1|
|     47|{6731e88756cb2d40...|Mystery|Thriller|Seven (a.k.a. Se7...|{6731d74e5d382ee9...|   5.0| 964983815|     1|
|     47|{6731ed1d9b262373...|Mystery|Thriller|Seven (a.k.a. 

### Create a new column named "Year"

In [13]:
from pyspark.sql.functions import substring
from pyspark.sql.functions import col

joined_df = joined_df.withColumn("year", substring("title", -5, 4))
joined_df = joined_df.filter(col("year").rlike("^[12]"))
joined_df = joined_df.withColumn("year", col("year").cast("int"))

joined_df.show()
# joined_df.select("year").distinct().show()

+-------+--------------------+------+--------------------+--------------------+------+----------+------+----+
|movieId|                 _id|genres|               title|                 _id|rating| timestamp|userId|year|
+-------+--------------------+------+--------------------+--------------------+------+----------+------+----+
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   0.5|1306463578|     3|1995|
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   3.0| 845553819|     6|1995|
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   2.5|1234334920|    28|1995|
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   4.0| 832059371|    40|1995|
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   3.0|1496205717|    47|1995|
|     31|{6731d7505d382ee9...| Drama|Dangerous Minds (...|{6731d74e5d382ee9...|   4.0| 847719088|    58|1995|
|     31|{

## Train a movie recommender model

### Linear Regression Model

In [14]:
# recommender = RecommendationEngine(joined_df)

In [15]:
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.regression import LinearRegression
from pyspark.ml.evaluation import RegressionEvaluator

In [ ]:
feature_assembler = VectorAssembler(inputCols=["userId", "movieId"], outputCol="features")
assembled_df = feature_assembler.transform(joined_df)
(training_data, test_data) = assembled_df.randomSplit([0.8, 0.2])

model = LinearRegression(featuresCol="features", labelCol="rating", predictionCol="prediction")
lr_model = model.fit(training_data)

Py4JJavaError: An error occurred while calling o103.fit.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 4 in stage 26.0 failed 1 times, most recent failure: Lost task 4.0 in stage 26.0 (TID 39) (10.127.155.247 executor driver): org.apache.spark.memory.SparkOutOfMemoryError: error while calling spill() on org.apache.spark.util.collection.unsafe.sort.UnsafeExternalSorter@f44785 : There is not enough space on the disk
	at org.apache.spark.memory.TaskMemoryManager.trySpillAndAcquire(TaskMemoryManager.java:254)
	at org.apache.spark.memory.TaskMemoryManager.acquireExecutionMemory(TaskMemoryManager.java:191)
	at org.apache.spark.memory.TaskMemoryManager.allocatePage(TaskMemoryManager.java:318)
	at org.apache.spark.memory.MemoryConsumer.allocatePage(MemoryConsumer.java:117)
	at org.apache.spark.util.collection.unsafe.sort.UnsafeExternalSorter.acquireNewPageIfNecessary(UnsafeExternalSorter.java:433)
	at org.apache.spark.util.collection.unsafe.sort.UnsafeExternal

In [ ]:
# make predictions
predictions = lr_model.transform(test_data)

# show predictions
predictions.select("features", "rating", "prediction").show()

# evaluate the model using R2 and RMSE
evaluator = RegressionEvaluator(labelCol="rating", predictionCol="prediction", metricName="rmse")
rmse = evaluator.evaluate(predictions)
print(f"Root Mean Squared Error (RMSE): {rmse}")

evaluator.setMetricName("r2")
r2 = evaluator.evaluate(predictions)
print(f"R2: {r2}")

+------------+------+------------------+
|    features|rating|        prediction|
+------------+------+------------------+
|  [6.0,31.0]|   3.0|3.5935924550276908|
|[162.0,31.0]|   4.0|3.5498632915061674|
|[337.0,31.0]|   5.0|3.5008081401198425|
|[483.0,31.0]|   2.0|3.4598821281061087|
|[109.0,31.0]|   3.0|3.5647199944974544|
|[181.0,31.0]|   3.0|3.5445373036413663|
|[426.0,31.0]|   5.0| 3.475860091700512|
|[447.0,31.0]|   4.0|3.4699734735341528|
|[131.0,31.0]|   3.0|3.5585530611803162|
|[159.0,31.0]|   3.5|3.5507042369585045|
|[162.0,31.0]|   4.0|3.5498632915061674|
|[181.0,31.0]|   3.0|3.5445373036413663|
|[203.0,31.0]|   3.5| 3.538370370324228|
|[307.0,31.0]|   1.5|3.5092175946432125|
|[314.0,31.0]|   3.0|3.5072553885877595|
|[437.0,31.0]|   4.0|3.4727766250419427|
|[447.0,31.0]|   4.0|3.4699734735341528|
|[464.0,31.0]|   4.0|  3.46520811597091|
|[561.0,31.0]|   2.5| 3.438017546345347|
|  [6.0,31.0]|   3.0|3.5935924550276908|
+------------+------+------------------+
only showing top

### ALS

In [ ]:
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml.recommendation import ALS
from pyspark.sql import Row

ratings = joined_df.select("userId", "movieId", "rating")
(training, test) = ratings.randomSplit([0.8, 0.2])

# set cold start strategy to 'drop' to ensure we don't get NaN evaluation metrics
als = ALS(maxIter=5, regParam=0.01, userCol="userId", itemCol="movieId", ratingCol="rating",
          coldStartStrategy="drop")
model = als.fit(training)

# evaluate
predictions = model.transform(test)
evaluator = RegressionEvaluator(metricName="rmse", labelCol="rating",
                                predictionCol="prediction")
rmse = evaluator.evaluate(predictions)
print("Root-mean-square error = " + str(rmse))

# top 10 movie recommendations for each user
userRecs = model.recommendForAllUsers(10)
# top 10 user recommendations for each movie
movieRecs = model.recommendForAllItems(10)

# top 10 movie recommendations for a specified set of users
users = ratings.select(als.getUserCol()).distinct().limit(3)
userSubsetRecs = model.recommendForUserSubset(users, 10)

# top 10 user recommendations for a specified set of movies
movies = ratings.select(als.getItemCol()).distinct().limit(3)
movieSubSetRecs = model.recommendForItemSubset(movies, 10)

Root-mean-square error = 0.538042612130651


In [ ]:
print(userRecs.show())

+------+--------------------+
|userId|     recommendations|
+------+--------------------+
|     1|[{945, 6.9002323}...|
|     2|[{6380, 7.6768894...|
|     3|[{92420, 6.368151...|
|     4|[{5666, 6.3266077...|
|     5|[{1243, 7.579549}...|
|     6|[{27611, 6.512519...|
|     7|[{130518, 8.39599...|
|     8|[{2693, 8.861821}...|
|     9|[{58301, 8.285681...|
|    10|[{26258, 7.073716...|
|    11|[{3476, 9.082434}...|
|    12|[{3925, 9.284978}...|
|    13|[{86377, 8.669381...|
|    14|[{1354, 9.348432}...|
|    15|[{1658, 8.423873}...|
|    16|[{2360, 4.6792865...|
|    17|[{3925, 6.625032}...|
|    18|[{3925, 5.659679}...|
|    19|[{130518, 4.88170...|
|    20|[{6370, 7.0244074...|
+------+--------------------+
only showing top 20 rows

None
